In [0]:
from pyspark.sql.functions import col, lower, trim

countries = spark.read.table("default.continents")
economies = spark.read.table("default.global_economy_indicators")

# Standardise and rename the country column in economies
economies_country = economies.select(trim(lower(col(" Country "))).alias("name")).distinct()

# Standardise the country names in countries too
countries_name = countries.select(trim(lower(col("name"))).alias("name")).distinct()

# Find mismatched country names
mismatched = economies_country.join(countries_name, on="name", how="left_anti")

display(mismatched)



name türkiye north macedonia kosovo zanzibar st. vincent and the grenadines state of palestine sudan (former) czechia republic of moldova ussr (former) syrian arab republic lao people's dr china, macao sar u.r. of tanzania: mainland venezuela (bolivarian republic of) bolivia (plurinational state of) micronesia (fs of) yemen arab republic (former) british virgin islands czechoslovakia (former) yugoslavia (former) yemen democratic (former) china, hong kong sar iran (islamic republic of) viet nam d.r. of the congo guinea-bissau former netherlands antilles ethiopia (former) russian federation republic of korea d.p.r. of korea

In [0]:
from pyspark.sql.functions import col, trim, lower

# First: trim and lowercase the actual "country" column (auto-correct spaces)
economies = economies.withColumn("country_clean", trim(lower(col(" Country "))))
countries = countries.withColumn("name_clean", trim(lower(col("name"))))

# Apply REPLACEMENTS to cleaned column
economies = economies.replace(
    {
        "türkiye": "turkey",
        "north macedonia": "macedonia",
        "state of palestine": "palestine, state of",
        "czechia": "czech republic",
        "republic of moldova": "moldova",
        "st. vincent and the grenadines": "saint vincent and the grenadines",
        "syrian arab republic": "syria",
        "lao people's dr": "laos",
        "china, macao sar": "macao",
        "u.r. of tanzania: mainland": "tanzania",
        "venezuela (bolivarian republic of)": "venezuela",
        "bolivia (plurinational state of)": "bolivia",
        "micronesia (fs of)": "micronesia (federated states of)",
        "yemen arab republic (former)": "yemen",
        "yemen democratic (former)": "yemen",
        "british virgin islands": "virgin islands (british)",
        "china, hong kong sar": "hong kong",
        "guinea-bissau": "guinea bissau",
        "ethiopia (former)": "ethiopia",
        "russian federation": "russia",
        "viet nam": "vietnam",
        "iran (islamic republic of)": "iran",
        "republic of korea": "south korea",
        "d.p.r. of korea": "north korea"
    },
    subset=["country_clean"]
)

countries = countries.replace(
    {
        "south korea": "north korea",
        "korea, republic of": "south korea"
    },
    subset=["name_clean"]
)

# Remove former/deprecated countries
remove_list = [
    "zanzibar", "south sudan", "sudan (former)", "czechoslovakia (former)",
    "yugoslavia (former)", "d.r. of the congo", "former netherlands antilles", "ussr (former)","kosovo"
]

economies = economies.filter(~col("country_clean").isin(remove_list))

# Get distinct country names for mismatch check
economies_country = economies.select("country_clean").distinct().withColumnRenamed("country_clean", "name")
countries_name = countries.select("name_clean").distinct().withColumnRenamed("name_clean", "name")

# Final mismatch
mismatched = economies_country.join(countries_name, on="name", how="left_anti")
display(mismatched)


name

In [0]:
countries.write.mode("overwrite").saveAsTable("default.countries")
# Clean column names: trim, remove leading/trailing spaces, and replace internal spaces with '-'

import re
# Fully clean each column name
def clean_col(col_name):
    col_name = col_name.strip()                   # Remove leading/trailing whitespace
    col_name = col_name.lower()                   # Lowercase for safety
    col_name = re.sub(r'\s+', '_', col_name)      # Replace spaces/tabs with underscores
    col_name = re.sub(r'[^a-zA-Z0-9_]', '', col_name)  # Remove special characters
    return col_name

# Apply cleaned column names to DataFrame
cleaned_cols = [clean_col(c) for c in economies.columns]
economies = economies.toDF(*cleaned_cols)


economies.write.mode("overwrite").saveAsTable("default.gdi2")



In [0]:
%sql 
use default;
SELECT *
FROM countries
where name_clean in ("south korea","north korea")

name alpha-2 alpha-3 country-code iso_3166-2 region sub-region intermediate-region region-code sub-region-code intermediate-region-code name_clean South Korea KP PRK 408 ISO 3166-2:KP Asia Eastern Asia null 142 30 null north korea Korea, Republic of KR KOR 410 ISO 3166-2:KR Asia Eastern Asia null 142 30 null south korea

In [0]:
%sql
-- Create new schema
CREATE SCHEMA IF NOT EXISTS global_development;

-- Country Mapping table 
CREATE OR REPLACE TABLE global_development.country_mapping AS
SELECT DISTINCT `alpha-3` AS country_code, name_clean AS name, region
FROM default.countries;

-- Tourism Table
CREATE OR REPLACE TABLE global_development.tourism AS
SELECT 
    ROW_NUMBER() OVER (ORDER BY c.country_code, t.year) AS id,
    c.country_code,
    CAST(t.year AS INT) AS year,
    CAST(t.tourism_receipts AS FLOAT) AS tourism_receipts,
    CAST(t.tourism_departures AS FLOAT) AS tourism_departures,
    CAST(t.tourism_arrivals AS FLOAT) AS tourism_arrivals
FROM global_development.country_mapping AS c
JOIN default.world_tourism_economy_data AS t ON t.country_code = c.country_code
WHERE t.year BETWEEN 2000 AND 2020;

-- Population Table
CREATE OR REPLACE TABLE global_development.population AS
SELECT 
    ROW_NUMBER() OVER (ORDER BY c.country_code, gdi1.year) AS id,
    c.country_code,
    CAST(gdi1.year AS INT) AS year,
    CAST(gdi1.calculated_gdp_per_capita AS FLOAT) AS gdp_per_capita,
    CAST(gdi2.per_capita_gni AS FLOAT) AS gni_per_capita,
    CAST(gdi1.population AS INT) AS population
FROM global_development.country_mapping AS c
JOIN default.global_development_indicators_2000_2020 AS gdi1 ON gdi1.country_code = c.country_code
JOIN default.gdi2 ON gdi2.country_clean = c.name AND CAST(gdi1.year AS INT) = CAST(gdi2.year AS INT)
WHERE gdi1.year BETWEEN 2000 AND 2020;

-- Social Progress Table
CREATE OR REPLACE TABLE global_development.social_progress AS
SELECT 
    ROW_NUMBER() OVER (ORDER BY c.country_code, gdi1.year) AS id,
    c.country_code,
    CAST(gdi1.year AS INT) AS year,
    CAST(gdi1.internet_usage_pct AS FLOAT) AS internet_usage_pct,
    CAST(gdi1.human_development_composite AS FLOAT) AS human_development_composite,
    CAST(gdi1.life_expectancy AS FLOAT) AS life_expectancy
FROM global_development.country_mapping AS c
JOIN default.global_development_indicators_2000_2020 AS gdi1 ON gdi1.country_code = c.country_code
WHERE gdi1.year BETWEEN 2000 AND 2020;

-- Economic Development Table
CREATE OR REPLACE TABLE global_development.economic_development AS
SELECT 
    ROW_NUMBER() OVER (ORDER BY c.country_code, gdi1.year) AS id,
    c.country_code,
    CAST(gdi1.year AS INT) AS year,
    gdi1.currency_unit,
    CAST(gdi2.gross_national_incomegni_in_usd AS FLOAT) AS gni_usd,
    CAST(gdi1.gdp_usd AS FLOAT) AS gdp_usd,
    CAST(gdi1.inflation_rate AS FLOAT) AS inflation_rate,
    CAST(gdi1.unemployment_rate AS FLOAT) AS unemployment_rate
FROM global_development.country_mapping AS c
JOIN default.global_development_indicators_2000_2020 AS gdi1 ON gdi1.country_code = c.country_code
JOIN default.gdi2 ON gdi2.country_clean = c.name AND CAST(gdi1.year AS INT) = CAST(gdi2.year AS INT)
WHERE gdi1.year BETWEEN 2000 AND 2020;

-- Environmental Progress Table
CREATE OR REPLACE TABLE global_development.environmental_progress AS
SELECT 
    ROW_NUMBER() OVER (ORDER BY c.country_code, gdi1.year) AS id,
    c.country_code,
    CAST(gdi1.year AS INT) AS year,
    CAST(gdi1.energy_use_per_capita AS FLOAT) AS energy_use_per_capita,
    CAST(gdi1.renewable_energy_pct AS FLOAT) AS renewable_energy_pct,
    CAST(gdi1.co2_emissions_per_capita_tons AS FLOAT) AS co2_emissions_per_capita_tons
FROM global_development.country_mapping AS c
JOIN default.global_development_indicators_2000_2020 AS gdi1 ON gdi1.country_code = c.country_code
WHERE gdi1.year BETWEEN 2000 AND 2020;


num_affected_rows num_inserted_rows

In [0]:
%sql
select * from gdi2

countryid country year ama_exchange_rate imf_based_exchange_rate population currency per_capita_gni agriculture__hunting__forestry__fishing_isic_ab changes_in_inventories construction_isic_f exports_of_goods_and_services final_consumption_expenditure general_government_final_consumption_expenditure gross_capital_formation gross_fixed_capital_formation_including_acquisitions_less_disposals_of_valuables household_consumption_expenditure_including_nonprofit_institutions_serving_households imports_of_goods_and_services manufacturing_isic_d mining__manufacturing__utilities_isic_ce other_activities_isic_jp total_value_added transport__storage_and_communication_isic_i wholesale__retail_trade__restaurants_and_hotels_isic_gh gross_national_incomegni_in_usd gross_domestic_product_gdp country_clean 4 Afghanistan 1970 0.044998427 0.044998427 10752971 Afghani 164 869917407 null 46793902 165618722 1663221269 112126986 94611818 94611818 1551094283 195277226 370146827 376690811 127747843 1731454254 83917200 226387091 1766527525 1731435587 afghanistan 4 Afghanistan 1971 0.044998427 0.044998427 11015857 Afghani 168 910828104 null 48994113 193580300 1796541240 121114833 99012350 99012350 1675426407 276296480 387549502 394401164 133754097 1812857077 87860382 237019196 1850121913 1812837521 afghanistan 4 Afghanistan 1972 0.044998427 0.044998427 11286753 Afghani 149 827945340 null 44535223 227654380 1607159399 108347543 103456794 103456794 1498811856 290370350 352284669 358512865 121582672 1647917912 79864525 215477287 1683947905 1647900178 afghanistan 4 Afghanistan 1973 0.044998427 0.044998427 11575305 Afghani 150 855486925 null 46018542 226913554 1617037233 109013455 121728433 121728433 1508023800 262962880 364010279 370445793 125630236 1702734673 82528885 222624293 1739998153 1702716294 afghanistan 4 Afghanistan 1974 0.044998427 0.044998427 11869879 Afghani 177 1035913365 null 55721659 284938449 1907408182 128588961 175061875 175061875 1778819221 305679151 440760406 448552790 152119162 2061751510 99918604 269525910 2106420227 2061729287 afghanistan 4 Afghanistan 1975 0.044998427 0.044998427 12157386 Afghani 195 1165441381 null 62686658 300493815 2131358499 143686711 221728484 221728484 1987671788 333827202 495891889 504659018 171142804 2319778374 112416374 303432162 2369877014 2319753506 afghanistan 4 Afghanistan 1976 0.044998427 0.044998427 12425267 Afghani 207 1262891632 null 67941997 329382802 2232098998 150478171 322716302 322716302 2081620805 370617399 537391228 546891983 185472327 2513608060 121865126 328544951 2568148611 2513580659 afghanistan 4 Afghanistan 1977 0.044998427 0.044998427 12687301 Afghani 231 1439687056 null 77430595 342962988 2584198550 174215156 362716078 362716078 2409983394 424938409 612470141 623298276 211382277 2864969897 138798518 374373152 2927408257 2864939207 afghanistan 4 Afghanistan 1978 0.044998427 0.044998427 12938862 Afghani 254 1618731870 null 87058287 354814847 2883951161 194423174 437531071 437531071 2689527987 453333379 688846878 701025415 237719665 3222997856 156155903 422306672 3292593311 3222963833 afghanistan 4 Afghanistan 1979 0.043730753 0.043730753 12986369 Afghani 285 1824507919 null 98215848 424287344 3241236374 218509730 487588175 487588175 3022726644 522344151 776522761 790251109 268036272 3630809406 176271742 473526514 3707542111 3630767856 afghanistan 4 Afghanistan 1980 0.044129167 0.044129167 12486631 Afghani 298 1833562539 null 98532815 421868016 3268912030 220375496 482304575 482304575 3048536534 526287844 779480093 793260866 269014824 3646833941 176313390 476149507 3722131465 3646796868 afghanistan 4 Afghanistan 1981 0.049479902 0.049479902 11155195 Afghani 314 1718724637 null 92428356 391421266 3066531139 206731957 459513054 459513054 2859799183 489983587 732043180 744985769 252555248 3427516574 166095276 452727309 3498878174 3427482014 afghanistan 4 Afghanistan 1982 0.050599608 0.050599608 10088289 Afghani 341 1726519723 null 93192698 396355483 3069066293 206902671 458169539 458169539 28

In [0]:
%sql
select * from countries

name alpha-2 alpha-3 country-code iso_3166-2 region sub-region intermediate-region region-code sub-region-code intermediate-region-code name_clean Afghanistan AF AFG 4 ISO 3166-2:AF Asia Southern Asia null 142 34 null afghanistan Åland Islands AX ALA 248 ISO 3166-2:AX Europe Northern Europe null 150 154 null åland islands Albania AL ALB 8 ISO 3166-2:AL Europe Southern Europe null 150 39 null albania Algeria DZ DZA 12 ISO 3166-2:DZ Africa Northern Africa null 2 15 null algeria American Samoa AS ASM 16 ISO 3166-2:AS Oceania Polynesia null 9 61 null american samoa Andorra AD AND 20 ISO 3166-2:AD Europe Southern Europe null 150 39 null andorra Angola AO AGO 24 ISO 3166-2:AO Africa Sub-Saharan Africa Middle Africa 2 202 17 angola Anguilla AI AIA 660 ISO 3166-2:AI Americas Latin America and the Caribbean Caribbean 19 419 29 anguilla Antarctica AQ ATA 10 ISO 3166-2:AQ null null null null null null antarctica Antigua and Barbuda AG ATG 28 ISO 3166-2:AG Americas Latin America and the Caribbean Caribbean 19 419 29 antigua and barbuda Argentina AR ARG 32 ISO 3166-2:AR Americas Latin America and the Caribbean South America 19 419 5 argentina Armenia AM ARM 51 ISO 3166-2:AM Asia Western Asia null 142 145 null armenia Aruba AW ABW 533 ISO 3166-2:AW Americas Latin America and the Caribbean Caribbean 19 419 29 aruba Australia AU AUS 36 ISO 3166-2:AU Oceania Australia and New Zealand null 9 53 null australia Austria AT AUT 40 ISO 3166-2:AT Europe Western Europe null 150 155 null austria Azerbaijan AZ AZE 31 ISO 3166-2:AZ Asia Western Asia null 142 145 null azerbaijan Bahamas BS BHS 44 ISO 3166-2:BS Americas Latin America and the Caribbean Caribbean 19 419 29 bahamas Bahrain BH BHR 48 ISO 3166-2:BH Asia Western Asia null 142 145 null bahrain Bangladesh BD BGD 50 ISO 3166-2:BD Asia Southern Asia null 142 34 null bangladesh Barbados BB BRB 52 ISO 3166-2:BB Americas Latin America and the Caribbean Caribbean 19 419 29 barbados Belarus BY BLR 112 ISO 3166-2:BY Europe Eastern Europe null 150 151 null belarus Belgium BE BEL 56 ISO 3166-2:BE Europe Western Europe null 150 155 null belgium Belize BZ BLZ 84 ISO 3166-2:BZ Americas Latin America and the Caribbean Central America 19 419 13 belize Benin BJ BEN 204 ISO 3166-2:BJ Africa Sub-Saharan Africa Western Africa 2 202 11 benin Bermuda BM BMU 60 ISO 3166-2:BM Americas Northern America null 19 21 null bermuda Bhutan BT BTN 64 ISO 3166-2:BT Asia Southern Asia null 142 34 null bhutan Bolivia BO BOL 68 ISO 3166-2:BO Americas Latin America and the Caribbean South America 19 419 5 bolivia Bonaire, Sint Eustatius and Saba BQ BES 535 ISO 3166-2:BQ Americas Latin America and the Caribbean Caribbean 19 419 29 bonaire, sint eustatius and saba Bosnia And Herzegovina BA BIH 70 ISO 3166-2:BA Europe Southern Europe null 150 39 null bosnia and herzegovina Botswana BW BWA 72 ISO 3166-2:BW Africa Sub-Saharan Africa Southern Africa 2 202 18 botswana Bouvet Island BV BVT 74 ISO 3166-2:BV Americas Latin America and the Caribbean South America 19 419 5 bouvet island Brazil BR BRA 76 ISO 3166-2:BR Americas Latin America and the Caribbean South America 19 419 5 brazil British Indian Ocean Territory IO IOT 86 ISO 3166-2:IO Africa Sub-Saharan Africa Eastern Africa 2 202 14 british indian ocean territory Brunei Darussalam BN BRN 96 ISO 3166-2:BN Asia South-eastern Asia null 142 35 null brunei darussalam Bulgaria BG BGR 100 ISO 3166-2:BG Europe Eastern Europe null 150 151 null bulgaria Burkina Faso BF BFA 854 ISO 3166-2:BF Africa Sub-Saharan Africa Western Africa 2 202 11 burkina faso Burundi BI BDI 108 ISO 3166-2:BI Africa Sub-Saharan Africa Eastern Africa 2 202 14 burundi Cabo Verde CV CPV 132 ISO 3166-2:CV Africa Sub-Saharan Africa Western Africa 2 202 11 cabo verde Cambodia KH KHM 116 ISO 3166-2:KH Asia South-eastern Asia null 142 35 null cambodia Cameroon CM CMR 120 ISO 3166-2:CM Africa Sub-Saharan Africa Middle Africa 2 202 17 cameroon Canada CA CAN 124 ISO 3166-2:CA Americas Northern America null 19 21 null canada Cayman Is